In [1]:
# Import packages

import pandas as pd 
import numpy as np 
import os
from bs4 import BeautifulSoup
import time
import requests
import nfl_data_py as nfl
import matplotlib.pyplot as plt
import plotly
import plotly.express as px

# Set certain settings for the notebook
pd.set_option("display.max_columns", None)

In [2]:
# Check current directory
os.getcwd()

'C:\\Users\\imacd_0odruq3\\Documents\\sports_gambling\\sports_gambling_algorithm'

In [3]:
# After looking at the ELO ratings and QB adjusted ELO ratings, it seems like just using those could create a valid 
# algorithm. However, there are so many other stats that are not incorporated into the ELO ratings. Using those stats in 
# place of or in addition to ELO ratings could possibly yield an even better algorithm. However, finding things like game 
# by game offense/defense rankings may be difficult, so this part of the project may require some web scraping. 

# Data I think could be useful
# Weather data
# Week by week offensive rankings
# Week by week defensive rankings
# Injuries

In [4]:
# # Scraping Weather Data 

# # Data is going to be scraped from http://www.nflweather.com/ 

start_season = 2014
end_season = 2022

season_total_weeks = {season: 17 for season in range(start_season, 2021)}
for season in range(2021, end_season):
    season_total_weeks[season] = 18
playoff_week_names = ['wildcard-weekend', 'divisional-playoffs', 'conf-championships', 'superbowl']

weather_table_dict_list = []

for season in range(start_season, end_season):
    for week in range(1, season_total_weeks[season]+5):
        print('{} Season, Week {}'.format(season, week))
        url_week = 'week-{}'.format(week) if week <= season_total_weeks[season] else playoff_week_names[(week - season_total_weeks[season]) - 1]
        r = requests.get('http://www.nflweather.com/en/week/{}/{}/'.format(season, url_week))
        soup = BeautifulSoup(r.content)
        if soup.find('table') is None:
            r = requests.get('http://www.nflweather.com/en/week/{}/%20{}/'.format(season, url_week))
            soup = BeautifulSoup(r.content)
        for game in soup.find('table').find_all('tr')[1:2]:
            away_team = game.select('a[href^="/en"]')[0].string
            home_team = game.select('a[href^="/en"]')[3].string
            info = game.find_all('td')
            temp_weather_string = info[9].string.strip()
            if temp_weather_string == 'DOME':
                temperature = 'DOME'
                weather = 'DOME'
            else:
                if (temp_weather_string[0:3]).isdigit():
                    temperature = int(temp_weather_string[0:3])
                    weather = temp_weather_string[5:]
                elif (temp_weather_string[0:2]).isdigit():
                    temperature = int(temp_weather_string[0:2])
                    weather = temp_weather_string[4:]
                elif (temp_weather_string[0]).isdigit():
                    temperature = int(temp_weather_string[0])
                    weather = temp_weather_string[3:]
            wind = int(info[11].string[0:2]) if (info[11].string[0:2]).isdigit() else int(info[11].string[0])
            
            weather_dict = {
                'season': season,
                'week': week,
                'home': home_team,
                'away': away_team,
                'temperature': temperature,
                'weather': weather,
                'wind': wind
                
            }
            weather_table_dict_list.append(weather_dict)
            
weather_df = pd.DataFrame.from_dict(weather_table_dict_list)

2014 Season, Week 1
[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Packers">Packers</a>
</td>
<td class="team-img"><a href="/en/team/Packers" style="text-decoration: none; color: #454545;"><img alt="Greenbay_6n_120" src="/system/teams/logos/000/000/024/list/GreenBay_6N_120.png?1377267883"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Seahawks" style="text-decoration: none; color: #454545;"><img alt="Seattle_6n_120a" src="/system/teams/logos/000/000/03

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Steelers">Steelers</a>
</td>
<td class="team-img"><a href="/en/team/Steelers" style="text-decoration: none; color: #454545;"><img alt="Pittsburg_ntc120" src="/system/teams/logos/000/000/014/list/Pittsburg_NTC120.png?1377268073"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Ravens" style="text-decoration: none; color: #454545;"><img alt="Baltimore_ntc120" src="/system/teams/logos/000/000/015/list/Baltimore

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Buccaneers">Buccaneers</a>
</td>
<td class="team-img"><a href="/en/team/Buccaneers" style="text-decoration: none; color: #454545;"><img alt="Tampa_bay_ntc120" src="/system/teams/logos/000/000/009/list/Tampa_Bay_NTC120.png?1377268184"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Falcons" style="text-decoration: none; color: #454545;"><img alt="Atlanta_ntc120a" src="/system/teams/logos/000/000/028/list/Atl

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Giants">Giants</a>
</td>
<td class="team-img"><a href="/en/team/Giants" style="text-decoration: none; color: #454545;"><img alt="New_york_g_6n__120" src="/system/teams/logos/000/000/021/list/New_York_G_6N__120.png?1377267939"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Washington" style="text-decoration: none; color: #454545;"><img alt="Redskins" src="/system/teams/logos/000/000/007/list/redskins.png?13

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Vikings">Vikings</a>
</td>
<td class="team-img"><a href="/en/team/Vikings" style="text-decoration: none; color: #454545;"><img alt="Minnesota_ntc120" src="/system/teams/logos/000/000/025/list/Minnesota_NTC120.png?1377267853"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Packers" style="text-decoration: none; color: #454545;"><img alt="Greenbay_6n_120" src="/system/teams/logos/000/000/024/list/GreenBay_6N_

...

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/49ers">49ers</a>
</td>
<td class="team-img"><a href="/en/team/49ers" style="text-decoration: none; color: #454545;"><img alt="San_francisco_6n_120" src="/system/teams/logos/000/000/030/list/San_Francisco_6N_120.png?1377267775"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Titans" style="text-decoration: none; color: #454545;"><img alt="Tennessee_ntc120" src="/system/teams/logos/000/000/005/list/Tennessee_

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Falcons">Falcons</a>
</td>
<td class="team-img"><a href="/en/team/Falcons" style="text-decoration: none; color: #454545;"><img alt="Atlanta_ntc120a" src="/system/teams/logos/000/000/028/list/Atlanta_NTC120A.png?1377267807"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Bills" style="text-decoration: none; color: #454545;"><img alt="Buffalo_red_ntc120" src="/system/teams/logos/000/000/003/list/Buffalo_red_N

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Chiefs">Chiefs</a>
</td>
<td class="team-img"><a href="/en/team/Chiefs" style="text-decoration: none; color: #454545;"><img alt="Kansas_city_ntc120" src="/system/teams/logos/000/000/001/list/Kansas_City_NTC120.png?1377268351"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Broncos" style="text-decoration: none; color: #454545;"><img alt="Denver_6n_120" src="/system/teams/logos/000/000/018/list/Denver_6N_120

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Raiders">Raiders</a>
</td>
<td class="team-img"><a href="/en/team/Raiders" style="text-decoration: none; color: #454545;"><img alt="Lv_b_wstripe_n_120" src="/system/teams/logos/000/000/019/list/LV_B_Wstripe_N_120.png?1599930229"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Bengals" style="text-decoration: none; color: #454545;"><img alt="Cinncinnati_6n_120" src="/system/teams/logos/000/000/012/list/Cinnc

[<tr>
<th> </th>
<th class="text-center" data-hide="phone,tablet">Away</th>
<th class="text-center" colspan="3">Game</th>
<th class="text-center" data-hide="phone,tablet">Home</th>
<th class="text-center" data-hide="phone">Time (ET)</th>
<th class="text-center" data-hide="phone,tablet">TV</th>
<th> </th>
<th class="text-center" data-hide="phone">Forecast</th>
<th data-hide="all">Extended Forecast</th>
<th class="text-center" data-hide="phone">Wind</th>
<th> </th>
</tr>, <tr>
<td class="team-img"> </td>
<td class="team-name text-center">
<a href="/en/team/Bengals">Bengals</a>
</td>
<td class="team-img"><a href="/en/team/Bengals" style="text-decoration: none; color: #454545;"><img alt="Cinncinnati_6n_120" src="/system/teams/logos/000/000/012/list/Cinncinnati_6N_120.png?1377268125"/></a></td>
<td class="team-vs">@</td>
<td class="team-img"><a href="/en/team/Chiefs" style="text-decoration: none; color: #454545;"><img alt="Kansas_city_ntc120" src="/system/teams/logos/000/000/001/list/Kansas

In [5]:
# See results

weather_df

season  week        home        away temperature        weather  wind
0      2014     1    Seahawks     Packers          70           Fair     5
1      2014     2      Ravens    Steelers          80  Mostly Cloudy     0
2      2014     3     Falcons  Buccaneers        DOME           DOME     3
3      2014     4  Washington      Giants          63       Overcast     7
4      2014     5     Packers     Vikings          63       Fog/Mist     7
..      ...   ...         ...         ...         ...            ...   ...
164    2021    18     Broncos      Chiefs          43          Foggy     2
165    2021    19     Bengals     Raiders          32  Mostly Cloudy     9
166    2021    20      Titans     Bengals          34          Clear     4
167    2021    21      Chiefs     Bengals          40  Partly Cloudy     5
168    2021    22     Bengals        Rams        DOME           DOME     7

[169 rows x 7 columns]

In [6]:
# Save created weather data frame as csv

weather_df.to_csv('../data/weather.csv')

In [7]:
# Use nfl_data_py package to get data

nfl_df = nfl.import_pbp_data([2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021])

2014 done.


C:\Users\imacd_0odruq3\anaconda3\lib\site-packages\nfl_data_py\__init__.py:115: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  plays = plays.append(raw)


2015 done.


C:\Users\imacd_0odruq3\anaconda3\lib\site-packages\nfl_data_py\__init__.py:115: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  plays = plays.append(raw)


2016 done.


...

2019 done.


C:\Users\imacd_0odruq3\anaconda3\lib\site-packages\nfl_data_py\__init__.py:115: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  plays = plays.append(raw)


2020 done.


C:\Users\imacd_0odruq3\anaconda3\lib\site-packages\nfl_data_py\__init__.py:115: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  plays = plays.append(raw)


2021 done.
Downcasting floats.


In [8]:
nfl_df

play_id          game_id old_game_id home_team away_team season_type  \
0          1.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
1         36.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
2         51.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
3         72.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
4         93.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
...        ...              ...         ...       ...       ...         ...   
50707   3930.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50708   3951.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50709   3968.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50710   3990.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50711   4011.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   

       week posteam posteam_type defteam side_of_field  yardline_100  \
0         1    None         None    None          None           NaN   
1         1     BUF         away     CHI           CHI          35.0   
2         1     BUF         away     CHI           BUF          80.0   
3         1     BUF         away     CHI           BUF          78.0   
4         1     BUF         away     CHI           BUF          76.0   
...     ...     ...          ...     ...           ...           ...   
50707    22     CIN         home      LA            LA          49.0   
50708    22    None         None    None          None           NaN   
50709    22     CIN         home      LA            LA          49.0   
50710    22      LA         away     CIN            LA          51.0   
50711    22    None         None    None          None           NaN   

        game_date  quarter_seconds_remaining  half_seconds_remaining  \
0      2014-09-07                      900.0                  1800.0   
1      2014-09-07                      900.0                  1800.0   
2      2014-09-07                      900.0                  1800.0   
3      2014-09-07                      867.0                  1767.0   
4      2014-09-07                      823.0                  1723.0   
...           ...                        ...                     ...   
50707  2022-02-13                       48.0                    48.0   
50708  2022-02-13                       43.0                    43.0   
50709  2022-02-13                       43.0                    43.0   
50710  2022-02-13                       39.0                    39.0   
50711  2022-02-13                        0.0                     0.0   

       game_seconds_remaining game_half  quarter_end  drive   sp  qtr  down  \
0                      3600.0     Half1          0.0    NaN  0.0  1.0   NaN   
1                      3600.0     Half1          0.0    1.0  0.0  1.0   NaN   
2                      3600.0     Half1          0.0    1.0  0.0  1.0   1.0   
3                      3567.0     Half1          0.0    1.0  0.0  1.0   2.0   
4                      3523.0     Half1          0.0    1.0  0.0  1.0   3.0   
...                       ...       ...          ...    ...  ...  ...   ...   
50707                    48.0     Half2          0.0   25.0  0.0  4.0   3.0   
50708                    43.0     Half2          0.0   25.0  0.0  4.0   NaN   
50709                    43.0     Half2          0.0   25.0  0.0  4.0   4.0   
50710                    39.0     Half2          0.0   26.0  0.0  4.0   1.0   
50711                     0.0     Half2          0.0   26.0  0.0  4.0   NaN   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
0             0.0  15:00  CHI 35      0.0     NaN   
1             0.0  15:00  CHI 35      0.0     4.0   
2             0.0  15:00  BUF 20     10.0     4.0   
3             0.0  14:27  BUF 22      8.0     4.0   
4             0.0  13:43  BUF 24      6.0     4.0   
...           ...    ...     ...      ...     ...   
50707   

In [9]:
# Add column detailing if there was a qb designed run

rosters = nfl.import_rosters([2020, 2021])
qb_roster = rosters[rosters.position == 'QB']
qb_roster = qb_roster[['position', 'player_name', 'player_id']].drop_duplicates()
qb_roster['player_id_string'] = qb_roster.apply(lambda x: str(x.player_id), axis=1)

def is_designed_qb_run(play, qb_roster):
    if play.rusher_id:
        if qb_roster.player_id_string.str.contains(str(play.rusher_id)).any():
            return 1 
    else: 
        return 0 
    
nfl_df['qb_designed_run'] = nfl_df.apply(lambda x: is_designed_qb_run(x, qb_roster), axis=1)

In [10]:
# Get important offensive NFL stats per game per team

# Get only offensive plays, take out qb kneels

offense = nfl_df[nfl_df.play_type.isin(['run', 'pass'])]
offense = offense[offense.qb_kneel == 0]
offense

play_id          game_id old_game_id home_team away_team season_type  \
2         51.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
3         72.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
4         93.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
6        141.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
7        162.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
...        ...              ...         ...       ...       ...         ...   
50704   3855.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50705   3884.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50706   3908.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50707   3930.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50709   3968.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   

       week posteam posteam_type defteam side_of_field  yardline_100  \
2         1     BUF         away     CHI           BUF          80.0   
3         1     BUF         away     CHI           BUF          78.0   
4         1     BUF         away     CHI           BUF          76.0   
6         1     CHI         home     BUF           CHI          66.0   
7         1     CHI         home     BUF           CHI          64.0   
...     ...     ...          ...     ...           ...           ...   
50704    22     CIN         home      LA           CIN          75.0   
50705    22     CIN         home      LA           CIN          58.0   
50706    22     CIN         home      LA            LA          49.0   
50707    22     CIN         home      LA            LA          49.0   
50709    22     CIN         home      LA            LA          49.0   

        game_date  quarter_seconds_remaining  half_seconds_remaining  \
2      2014-09-07                      900.0                  1800.0   
3      2014-09-07                      867.0                  1767.0   
4      2014-09-07                      823.0                  1723.0   
6      2014-09-07                      810.0                  1710.0   
7      2014-09-07                      768.0                  1668.0   
...           ...                        ...                     ...   
50704  2022-02-13                       85.0                    85.0   
50705  2022-02-13                       79.0                    79.0   
50706  2022-02-13                       54.0                    54.0   
50707  2022-02-13                       48.0                    48.0   
50709  2022-02-13                       43.0                    43.0   

       game_seconds_remaining game_half  quarter_end  drive   sp  qtr  down  \
2                      3600.0     Half1          0.0    1.0  0.0  1.0   1.0   
3                      3567.0     Half1          0.0    1.0  0.0  1.0   2.0   
4                      3523.0     Half1          0.0    1.0  0.0  1.0   3.0   
6                      3510.0     Half1          0.0    2.0  0.0  1.0   1.0   
7                      3468.0     Half1          0.0    2.0  0.0  1.0   2.0   
...                       ...       ...          ...    ...  ...  ...   ...   
50704                    85.0     Half2          0.0   25.0  0.0  4.0   1.0   
50705                    79.0     Half2          0.0   25.0  0.0  4.0   1.0   
50706                    54.0     Half2          0.0   25.0  0.0  4.0   2.0   
50707                    48.0     Half2          0.0   25.0  0.0  4.0   3.0   
50709                    43.0     Half2          0.0   25.0  0.0  4.0   4.0   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
2             0.0  15:00  BUF 20     10.0     4.0   
3             0.0  14:27  BUF 22      8.0     4.0   
4             0.0  13:43  BUF 24      6.0     4.0   
6             0.0  13:30  CHI 34     10.0    66.0   
7             0.0  12:48  CHI 36      8.0    66.0   
...           ...    ...     ...      ...     ...   
50704   

In [11]:
# Get rushing stats

# Total rushes, total rush yards, rushing epa

rushes = offense[offense.play_type == 'run']
rushing_grouped = rushes.groupby(by=['season', 'week', 'posteam'])
rush_df = rushing_grouped.count()['play_id'].rename('total_rushes').to_frame()
rush_df[['total_rush_yards', 'rushing_epa', 'rush_tds']] = rushing_grouped.sum()[['yards_gained', 'epa', 'rush_touchdown']]

rush_df

total_rushes  total_rush_yards  rushing_epa  rush_tds
season week posteam                                                       
2014   1    ARI                26             110.0    -7.697317       0.0
            ATL                25             123.0     2.559394       1.0
            BAL                21              94.0    -0.093163       1.0
            BUF                31             197.0     4.315138       1.0
            CAR                33             113.0    -6.247634       0.0
...                           ...               ...          ...       ...
2021   21   KC                 24             139.0     4.338426       0.0
            LA                 26              76.0    -7.967496       0.0
            SF                 20              50.0    -9.073356       0.0
       22   CIN                19              80.0    -1.797324       0.0
            LA                 22              44.0    -8.289258       0.0

[4312 rows x 4 columns]

In [12]:
# Get passing stats

# Total pass attempts, total pass yards, passing epa

passing = offense[offense.play_type == 'pass']
passing_grouped = passing.groupby(by=['season', 'week', 'posteam'])
passing_grouped_no_sacks = passing[passing.sack == 0].groupby(by=['season', 'week', 'posteam'])
pass_df = passing_grouped_no_sacks.count()['play_id'].rename('total_pass_attempts').to_frame()
pass_df['total_passing_yards'] = passing_grouped_no_sacks.sum()['yards_gained']
pass_df[['completions', 'passing_epa', 'pass_tds']] = passing_grouped.sum()[['complete_pass', 'epa', 'pass_touchdown']]
pass_df['avg_cpoe'] = passing_grouped_no_sacks.mean()['cpoe'].rename('avg_cpoe').to_frame()

pass_df

total_pass_attempts  total_passing_yards  completions  \
season week posteam                                                          
2014   1    ARI                       38                304.0         24.0   
            ATL                       42                448.0         31.0   
            BAL                       62                345.0         35.0   
            BUF                       22                173.0         16.0   
            CAR                       33                230.0         24.0   
...                                  ...                  ...          ...   
2021   21   KC                        39                275.0         26.0   
            LA                        45                337.0         31.0   
            SF                        29                232.0         16.0   
       22   CIN                       34                269.0         23.0   
            LA                        42                283.0         26.0   

                     passing_epa  pass_tds   avg_cpoe  
season week posteam                                    
2014   1    ARI         6.098425       2.0   3.160065  
            ATL        17.253965       3.0   6.128030  
            BAL        -4.871387       1.0 -11.889451  
            BUF         0.368607       1.0  11.150598  
            CAR         8.423189       2.0   9.822589  
...                          ...       ...        ...  
2021   21   KC         -6.372242       3.0   0.665231  
            LA         13.104126       2.0   6.444983  
            SF          6.194037       2.0 -18.026171  
       22   CIN        -9.384247       2.0  -1.240713  
            LA          3.046524       3.0  -2.291202  

[4312 rows x 6 columns]

In [13]:
# Get other offensive stats

# Get qb epa 
qb_stats = offense[(offense.play_type == 'pass') | (offense.qb_scramble == 1) | (offense.qb_designed_run == 1)]
qb_epa_df = qb_stats.groupby(by = ['season', 'week', 'posteam']).sum()['epa'].rename('qb_epa').to_frame()

# Get sacks, interceptions, fumbles, fumbles lost, turnovers
turnovers_df = offense.groupby(by = ['season', 'week', 'posteam']).sum()[['sack', 'fumble', 'fumble_lost', 'interception']]
turnovers_df.columns = ['sacks_allowed', 'fumbles', 'lost_fumbles', 'interceptions_thrown']
turnovers_df

sacks_allowed  fumbles  lost_fumbles  \
season week posteam                                         
2014   1    ARI                2.0      2.0           2.0   
            ATL                1.0      1.0           1.0   
            BAL                3.0      1.0           1.0   
            BUF                1.0      0.0           0.0   
            CAR                1.0      1.0           0.0   
...                            ...      ...           ...   
2021   21   KC                 4.0      2.0           0.0   
            LA                 2.0      0.0           0.0   
            SF                 0.0      0.0           0.0   
       22   CIN                7.0      0.0           0.0   
            LA                 2.0      0.0           0.0   

                     interceptions_thrown  
season week posteam                        
2014   1    ARI                       0.0  
            ATL                       0.0  
            BAL                       1.0  
            BUF                       1.0  
            CAR                       0.0  
...                                   ...  
2021   21   KC                        2.0  
            LA                        1.0  
            SF                        1.0  
       22   CIN                       0.0  
            LA                        2.0  

[4312 rows x 4 columns]

In [14]:
# Get important defensive NFL stats per game per team

# Get only defensive plays, take out qb kneels

defense = nfl_df[nfl_df.play_type.isin(['run', 'pass'])]
defense = defense[defense.qb_kneel == 0]
defense

play_id          game_id old_game_id home_team away_team season_type  \
2         51.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
3         72.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
4         93.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
6        141.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
7        162.0  2014_01_BUF_CHI  2014090702       CHI       BUF         REG   
...        ...              ...         ...       ...       ...         ...   
50704   3855.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50705   3884.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50706   3908.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50707   3930.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   
50709   3968.0   2021_22_LA_CIN  2022021301       CIN        LA        POST   

       week posteam posteam_type defteam side_of_field  yardline_100  \
2         1     BUF         away     CHI           BUF          80.0   
3         1     BUF         away     CHI           BUF          78.0   
4         1     BUF         away     CHI           BUF          76.0   
6         1     CHI         home     BUF           CHI          66.0   
7         1     CHI         home     BUF           CHI          64.0   
...     ...     ...          ...     ...           ...           ...   
50704    22     CIN         home      LA           CIN          75.0   
50705    22     CIN         home      LA           CIN          58.0   
50706    22     CIN         home      LA            LA          49.0   
50707    22     CIN         home      LA            LA          49.0   
50709    22     CIN         home      LA            LA          49.0   

        game_date  quarter_seconds_remaining  half_seconds_remaining  \
2      2014-09-07                      900.0                  1800.0   
3      2014-09-07                      867.0                  1767.0   
4      2014-09-07                      823.0                  1723.0   
6      2014-09-07                      810.0                  1710.0   
7      2014-09-07                      768.0                  1668.0   
...           ...                        ...                     ...   
50704  2022-02-13                       85.0                    85.0   
50705  2022-02-13                       79.0                    79.0   
50706  2022-02-13                       54.0                    54.0   
50707  2022-02-13                       48.0                    48.0   
50709  2022-02-13                       43.0                    43.0   

       game_seconds_remaining game_half  quarter_end  drive   sp  qtr  down  \
2                      3600.0     Half1          0.0    1.0  0.0  1.0   1.0   
3                      3567.0     Half1          0.0    1.0  0.0  1.0   2.0   
4                      3523.0     Half1          0.0    1.0  0.0  1.0   3.0   
6                      3510.0     Half1          0.0    2.0  0.0  1.0   1.0   
7                      3468.0     Half1          0.0    2.0  0.0  1.0   2.0   
...                       ...       ...          ...    ...  ...  ...   ...   
50704                    85.0     Half2          0.0   25.0  0.0  4.0   1.0   
50705                    79.0     Half2          0.0   25.0  0.0  4.0   1.0   
50706                    54.0     Half2          0.0   25.0  0.0  4.0   2.0   
50707                    48.0     Half2          0.0   25.0  0.0  4.0   3.0   
50709                    43.0     Half2          0.0   25.0  0.0  4.0   4.0   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
2             0.0  15:00  BUF 20     10.0     4.0   
3             0.0  14:27  BUF 22      8.0     4.0   
4             0.0  13:43  BUF 24      6.0     4.0   
6             0.0  13:30  CHI 34     10.0    66.0   
7             0.0  12:48  CHI 36      8.0    66.0   
...           ...    ...     ...      ...     ...   
50704   

In [15]:
# Get rushing defense stats

# Total rushes, total rush yards, rushing epa

rushes_def = defense[defense.play_type == 'run']
rushing_grouped_def = rushes.groupby(by=['season', 'week', 'defteam'])
rush_df_def = rushing_grouped_def.count()['play_id'].rename('total_rushes_allowed').to_frame()
rush_df_def[['total_rush_yards_allowed', 'rushing_epa_allowed', 'rush_tds_allowed']] = rushing_grouped_def.sum()[['yards_gained', 'epa', 'rush_touchdown']]

rush_df_def

total_rushes_allowed  total_rush_yards_allowed  \
season week defteam                                                   
2014   1    ARI                        24                      52.0   
            ATL                        28                     139.0   
            BAL                        24                      81.0   
            BUF                        18                      86.0   
            CAR                        17                     102.0   
...                                   ...                       ...   
2021   21   KC                         27                     116.0   
            LA                         20                      50.0   
            SF                         26                      76.0   
       22   CIN                        22                      44.0   
            LA                         19                      80.0   

                     rushing_epa_allowed  rush_tds_allowed  
season week defteam                                         
2014   1    ARI                -8.805075               1.0  
            ATL                 4.264254               3.0  
            BAL                -4.888501               0.0  
            BUF                -0.055888               0.0  
            CAR                 1.025410               0.0  
...                                  ...               ...  
2021   21   KC                  1.386047               0.0  
            LA                 -9.073356               0.0  
            SF                 -7.967496               0.0  
       22   CIN                -8.289258               0.0  
            LA                 -1.797324               0.0  

[4312 rows x 4 columns]

In [16]:
# Get passing defense stats

# Total pass attempts, total pass yards, passing epa

passing_def = defense[defense.play_type == 'pass']
passing_grouped_def = passing_def.groupby(by=['season', 'week', 'defteam'])
passing_grouped_def_no_sacks = passing_def[passing_def.sack == 0].groupby(by=['season', 'week', 'defteam'])
pass_df_def = passing_grouped_def_no_sacks.count()['play_id'].rename('total_pass_attempts_allowed').to_frame()
pass_df_def['passing_yards_allowed'] = passing_grouped_def_no_sacks.sum()['yards_gained']
pass_df_def[['completions_allowed', 'passing_epa_allowed', 'pass_tds_allowed']] = passing_grouped_def.sum()[['complete_pass', 'epa', 'pass_touchdown']]
pass_df_def['avg_cpoe_allowed'] = passing_grouped_def.mean()['cpoe'].rename('avg_cpoe').to_frame()

pass_df_def

total_pass_attempts_allowed  passing_yards_allowed  \
season week defteam                                                       
2014   1    ARI                               36                  238.0   
            ATL                               42                  333.0   
            BAL                               39                  303.0   
            BUF                               49                  349.0   
            CAR                               35                  183.0   
...                                          ...                    ...   
2021   21   KC                                39                  252.0   
            LA                                29                  232.0   
            SF                                45                  337.0   
       22   CIN                               42                  283.0   
            LA                                34                  269.0   

                     completions_allowed  passing_epa_allowed  \
season week defteam                                             
2014   1    ARI                     21.0             0.799435   
            ATL                     29.0             9.202585   
            BAL                     25.0            11.252419   
            BUF                     34.0            -6.755498   
            CAR                     22.0           -10.437735   
...                                  ...                  ...   
2021   21   KC                      23.0             3.913528   
            LA                      16.0             6.194037   
            SF                      31.0            13.104126   
       22   CIN                     26.0             3.046524   
            LA                      23.0            -9.384247   

                     pass_tds_allowed  avg_cpoe_allowed  
season week defteam                                      
2014   1    ARI                   1.0         -6.609174  
            ATL                   1.0         -0.291977  
            BAL                   1.0         -2.044219  
            BUF                   2.0          2.864331  
            CAR                   2.0          0.519191  
...                               ...               ...  
2021   21   KC                    2.0         -1.847335  
            LA                    2.0        -18.026171  
            SF                    2.0          6.444983  
       22   CIN                   3.0         -2.291202  
            LA                    2.0         -1.240713  

[4312 rows x 6 columns]

In [17]:
# Get other defensive stats

# Get qb epa 
qb_stats_def = defense[(defense.play_type == 'pass') | (defense.qb_scramble == 1) | (defense.qb_designed_run == 1)]
qb_epa_df_def = qb_stats_def.groupby(by = ['season', 'week', 'defteam']).sum()['epa'].rename('qb_epa_allowed').to_frame()

# Get sacks, interceptions, fumbles, fumbles lost, turnovers
turnovers_df_def = defense.groupby(by = ['season', 'week', 'defteam']).sum()[['sack', 'fumble_forced', 'interception']]
turnovers_df_def.columns = ['sacks', 'fumbles_forced', 'interceptions']
fumble_recovery_df = defense[(defense.defteam == defense.fumble_recovery_1_team)].groupby(by = ['season', 'week', 'defteam']).sum()['fumble_forced'].rename('fumbles_recovered').to_frame()
turnovers_df_def = turnovers_df_def.join(fumble_recovery_df, how='left').fillna(0)
turnovers_df_def

sacks  fumbles_forced  interceptions  fumbles_recovered
season week defteam                                                         
2014   1    ARI        0.0             0.0            1.0                0.0
            ATL        0.0             1.0            1.0                1.0
            BAL        0.0             0.0            0.0                0.0
            BUF        2.0             1.0            2.0                1.0
            CAR        3.0             2.0            2.0                1.0
...                    ...             ...            ...                ...
2021   21   KC         1.0             0.0            1.0                0.0
            LA         0.0             0.0            1.0                0.0
            SF         2.0             0.0            1.0                0.0
       22   CIN        2.0             0.0            2.0                0.0
            LA         7.0             0.0            0.0                0.0

[4312 rows x 4 columns]

In [18]:
# Get special teams stats

specials = nfl_df[nfl_df.special == 1]
specials_grouped = specials.groupby(by = ['season', 'week', 'posteam'])
specials_epa_df_one = specials_grouped.sum()['epa'].rename('special_teams_epa_one').to_frame()

specials = nfl_df[nfl_df.special == 1]
specials_grouped = specials.groupby(by = ['season', 'week', 'defteam'])
specials_epa_df_two = specials_grouped.sum()['epa'].rename('special_teams_epa_two').to_frame()

specials_epa_df = specials_epa_df_one.merge(specials_epa_df_two, left_on=['season', 'week', 'posteam'], right_index=True)
specials_epa_df['special_teams_epa'] = specials_epa_df.special_teams_epa_one - specials_epa_df.special_teams_epa_two
specials_epa_df.drop(columns = ['special_teams_epa_one', 'special_teams_epa_two'], inplace=True)
specials_epa_df

special_teams_epa
season week posteam                   
2014   1    ARI              -4.751772
            ATL              -1.162613
            BAL              -2.107624
            BUF               3.721131
            CAR              -3.457676
...                                ...
2021   21   KC               -2.057830
            LA               -0.072526
            SF                0.072526
       22   CIN               1.208638
            LA               -1.208638

[4312 rows x 1 columns]

In [19]:
# Get overall score and other game total stats

home_scores_and_etc_df = nfl_df.groupby(by = ['season', 'week', 'home_team', 'away_team']).max()[['home_score', 'away_score']]
home_scores_and_etc_df.index.names = ['season', 'week', 'team', 'opponent']
home_scores_and_etc_df.columns = ['score', 'opponent_score']
away_scores_and_etc_df = nfl_df.groupby(by = ['season', 'week', 'away_team', 'home_team']).max()[['away_score', 'home_score']]
away_scores_and_etc_df.index.names = ['season', 'week', 'team', 'opponent']
away_scores_and_etc_df.columns = ['score', 'opponent_score']

final_nfl_df = pd.concat([home_scores_and_etc_df, away_scores_and_etc_df])
final_nfl_df = final_nfl_df.sort_index()
final_nfl_df

<ipython-input-19-85bf0e779c49>:3: FutureWarning: Dropping invalid columns in DataFrameGroupBy.max is deprecated. In a future version, a TypeError will be raised. Before calling .max, select only columns which should be valid for the function.
  home_scores_and_etc_df = nfl_df.groupby(by = ['season', 'week', 'home_team', 'away_team']).max()[['home_score', 'away_score']]
<ipython-input-19-85bf0e779c49>:6: FutureWarning: Dropping invalid columns in DataFrameGroupBy.max is deprecated. In a future version, a TypeError will be raised. Before calling .max, select only columns which should be valid for the function.
  away_scores_and_etc_df = nfl_df.groupby(by = ['season', 'week', 'away_team', 'home_team']).max()[['away_score', 'home_score']]


score  opponent_score
season week team opponent                       
2014   1    ARI  LAC          18              17
            ATL  NO           37              34
            BAL  CIN          16              23
            BUF  CHI          23              20
            CAR  TB           20              14
...                          ...             ...
2021   21   KC   CIN          24              27
            LA   SF           20              17
            SF   LA           17              20
       22   CIN  LA           20              23
            LA   CIN          23              20

[4312 rows x 2 columns]

In [20]:
# Combine all stats together into one data frame

final_nfl_df = final_nfl_df.merge(
    pass_df, left_on=['season', 'week', 'team'], right_index=True).merge(
    rush_df, left_on=['season', 'week', 'team'], right_index=True).merge(
    qb_epa_df, left_on=['season', 'week', 'team'], right_index=True).merge(
    turnovers_df, left_on=['season', 'week', 'team'], right_index=True).merge(
    rush_df_def, left_on=['season', 'week', 'team'], right_index=True).merge(
    pass_df_def, left_on=['season', 'week', 'team'], right_index=True).merge(
    turnovers_df_def, left_on=['season', 'week', 'team'], right_index=True).merge(
    specials_epa_df, left_on=['season', 'week', 'team'], right_index=True)

final_nfl_df

score  opponent_score  total_pass_attempts  \
season week team opponent                                               
2014   1    ARI  LAC          18              17                   38   
            ATL  NO           37              34                   42   
            BAL  CIN          16              23                   62   
            BUF  CHI          23              20                   22   
            CAR  TB           20              14                   33   
...                          ...             ...                  ...   
2021   21   KC   CIN          24              27                   39   
            LA   SF           20              17                   45   
            SF   LA           17              20                   29   
       22   CIN  LA           20              23                   34   
            LA   CIN          23              20                   42   

                           total_passing_yards  completions  passing_epa  \
season week team opponent                                                  
2014   1    ARI  LAC                     304.0         24.0     6.098425   
            ATL  NO                      448.0         31.0    17.253965   
            BAL  CIN                     345.0         35.0    -4.871387   
            BUF  CHI                     173.0         16.0     0.368607   
            CAR  TB                      230.0         24.0     8.423189   
...                                        ...          ...          ...   
2021   21   KC   CIN                     275.0         26.0    -6.372242   
            LA   SF                      337.0         31.0    13.104126   
            SF   LA                      232.0         16.0     6.194037   
       22   CIN  LA                      269.0         23.0    -9.384247   
            LA   CIN                     283.0         26.0     3.046524   

                           pass_tds   avg_cpoe  total_rushes  \
season week team opponent                                      
2014   1    ARI  LAC            2.0   3.160065            26   
            ATL  NO             3.0   6.128030            25   
            BAL  CIN            1.0 -11.889451            21   
            BUF  CHI            1.0  11.150598            31   
            CAR  TB             2.0   9.822589            33   
...                             ...        ...           ...   
2021   21   KC   CIN            3.0   0.665231            24   
            LA   SF             2.0   6.444983            26   
            SF   LA             2.0 -18.026171            20   
       22   CIN  LA             2.0  -1.240713            19   
            LA   CIN            3.0  -2.291202            22   

                           total_rush_yards  rushing_epa  rush_tds     qb_epa  \
season week team opponent                                                       
2014   1    ARI  LAC                  110.0    -7.697317       0.0   7.779734   
            ATL  NO                   123.0     2.559394       1.0  17.526014   
            BAL  CIN                   94.0    -0.093163       1.0  -3.078329   
            BUF  CHI                  197.0     4.315138       1.0   0.591515   
            CAR  TB                   113.0    -6.247634       0.0  10.352312   
...                                     ...          ...       ...        ...   
2021   21   KC   CIN                  139.0     4.338426       0.0  -5.461161   
            LA   SF                    76.0    -7.967496       0.0  11.619948   
            SF   LA                    50.0    -9.073356       0.0   5.722747   
       22   CIN  LA                    80.0    -1.797324       0.0  -7.677874   
            LA   CIN                   44.0    -8.289258       0.0   3.074575   

                           sacks_allowed  fumbles  lost_fumbles  \
season week team opponent                                         
2014   1    ARI  LAC                 2.0      2.0           2.0   


In [21]:
# Flip sign of def epa 

final_nfl_df['passing_epa_def'] = -final_nfl_df['passing_epa_allowed']
final_nfl_df['rushing_epa_def'] = -final_nfl_df['rushing_epa_allowed']

# Add total epa stats

final_nfl_df['total_epa'] = final_nfl_df.apply(lambda x: x.passing_epa + x.rushing_epa + x.special_teams_epa + x.rushing_epa_def + x.passing_epa_def, axis = 1)
final_nfl_df['total_opposing_epa'] = -final_nfl_df.total_epa

In [22]:
final_nfl_df.loc[[(2021, 2, 'NYG', 'WAS'), (2021, 2, 'WAS', 'NYG')]]

score  opponent_score  total_pass_attempts  \
season week team opponent                                               
2021   2    NYG  WAS          29              30                   32   
            WAS  NYG          30              29                   45   

                           total_passing_yards  completions  passing_epa  \
season week team opponent                                                  
2021   2    NYG  WAS                     249.0         22.0     2.820566   
            WAS  NYG                     336.0         34.0     0.782703   

                           pass_tds  avg_cpoe  total_rushes  total_rush_yards  \
season week team opponent                                                       
2021   2    NYG  WAS            1.0  4.384123            27             164.0   
            WAS  NYG            2.0  7.751751            22              87.0   

                           rushing_epa  rush_tds    qb_epa  sacks_allowed  \
season week team opponent                                                   
2021   2    NYG  WAS          2.228114       1.0  8.245204            4.0   
            WAS  NYG          5.956827       1.0  2.842495            1.0   

                           fumbles  lost_fumbles  interceptions_thrown  \
season week team opponent                                                
2021   2    NYG  WAS           0.0           0.0                   0.0   
            WAS  NYG           0.0           0.0                   1.0   

                           total_rushes_allowed  total_rush_yards_allowed  \
season week team opponent                                                   
2021   2    NYG  WAS                         22                      87.0   
            WAS  NYG                         27                     164.0   

                           rushing_epa_allowed  rush_tds_allowed  \
season week team opponent                                          
2021   2    NYG  WAS                  5.956827               1.0   
            WAS  NYG                  2.228114               1.0   

                           total_pass_attempts_allowed  passing_yards_allowed  \
season week team opponent                                                       
2021   2    NYG  WAS                                45                  336.0   
            WAS  NYG                                32                  249.0   

                           completions_allowed  passing_epa_allowed  \
season week team opponent                                             
2021   2    NYG  WAS                      34.0             0.782703   
            WAS  NYG                      22.0             2.820566   

                           pass_tds_allowed  avg_cpoe_allowed  sacks  \
season week team opponent                                              
2021   2    NYG  WAS                    2.0          7.751751    1.0   
            WAS  NYG                    1.0          4.384123    4.0   

                           fumbles_forced  interceptions  fumbles_recovered  \
season week team opponent                                                     
2021   2    NYG  WAS                  0.0            1.0                0.0   
            WAS  NYG                  0.0            0.0                0.0   

                           special_teams_epa  passing_epa_def  \
season week team opponent                                       
2021   2    NYG  WAS                2.560868        -0.782703   
            WAS  NYG               -2.560868        -2.820566   

                           rushing_epa_def  total_epa  total_opposing_epa  
season week team opponent                                                  
2021   2    NYG  WAS             -5.956827   0.870017           -0.870017  
            WAS  NYG             -2.228114  -0.870017            0.870017

In [23]:
final_nfl_df

score  opponent_score  total_pass_attempts  \
season week team opponent                                               
2014   1    ARI  LAC          18              17                   38   
            ATL  NO           37              34                   42   
            BAL  CIN          16              23                   62   
            BUF  CHI          23              20                   22   
            CAR  TB           20              14                   33   
...                          ...             ...                  ...   
2021   21   KC   CIN          24              27                   39   
            LA   SF           20              17                   45   
            SF   LA           17              20                   29   
       22   CIN  LA           20              23                   34   
            LA   CIN          23              20                   42   

                           total_passing_yards  completions  passing_epa  \
season week team opponent                                                  
2014   1    ARI  LAC                     304.0         24.0     6.098425   
            ATL  NO                      448.0         31.0    17.253965   
            BAL  CIN                     345.0         35.0    -4.871387   
            BUF  CHI                     173.0         16.0     0.368607   
            CAR  TB                      230.0         24.0     8.423189   
...                                        ...          ...          ...   
2021   21   KC   CIN                     275.0         26.0    -6.372242   
            LA   SF                      337.0         31.0    13.104126   
            SF   LA                      232.0         16.0     6.194037   
       22   CIN  LA                      269.0         23.0    -9.384247   
            LA   CIN                     283.0         26.0     3.046524   

                           pass_tds   avg_cpoe  total_rushes  \
season week team opponent                                      
2014   1    ARI  LAC            2.0   3.160065            26   
            ATL  NO             3.0   6.128030            25   
            BAL  CIN            1.0 -11.889451            21   
            BUF  CHI            1.0  11.150598            31   
            CAR  TB             2.0   9.822589            33   
...                             ...        ...           ...   
2021   21   KC   CIN            3.0   0.665231            24   
            LA   SF             2.0   6.444983            26   
            SF   LA             2.0 -18.026171            20   
       22   CIN  LA             2.0  -1.240713            19   
            LA   CIN            3.0  -2.291202            22   

                           total_rush_yards  rushing_epa  rush_tds     qb_epa  \
season week team opponent                                                       
2014   1    ARI  LAC                  110.0    -7.697317       0.0   7.779734   
            ATL  NO                   123.0     2.559394       1.0  17.526014   
            BAL  CIN                   94.0    -0.093163       1.0  -3.078329   
            BUF  CHI                  197.0     4.315138       1.0   0.591515   
            CAR  TB                   113.0    -6.247634       0.0  10.352312   
...                                     ...          ...       ...        ...   
2021   21   KC   CIN                  139.0     4.338426       0.0  -5.461161   
            LA   SF                    76.0    -7.967496       0.0  11.619948   
            SF   LA                    50.0    -9.073356       0.0   5.722747   
       22   CIN  LA                    80.0    -1.797324       0.0  -7.677874   
            LA   CIN                   44.0    -8.289258       0.0   3.074575   

                           sacks_allowed  fumbles  lost_fumbles  \
season week team opponent                                         
2014   1    ARI  LAC                 2.0      2.0           2.0   


In [25]:
# Save data frame 

final_nfl_df.to_csv('../data/nfl_per_game_stats.csv')